# Plotly

In [1]:
import plotly.express as px
import pandas as pd
import numpy as np

# 折れ線グラフ
連続した数値の変化を表す定番グラフ。ただし、ラベルの種類数が10を超えたあたりから線が重なるなどで見づらくなる。<br>
推奨数は5で、それ以上の場合はグラフを複数に分けるほうが無難<br>
データはhttps://gist.github.com/mbostock/3884955 からのもので、ある時期の各地域の温度（°F）の関係図

In [2]:
plot_df = pd.read_csv('data/plot.csv')
plot_df['date'] = pd.to_datetime(plot_df['date'], format='%Y%m%d')
display(plot_df.head())
melt_plot_df = plot_df.melt(
    id_vars='date',
    var_name='city',
    value_name='temperature'
    )
print('melt処理')
display(melt_plot_df.head())

date  New York  San Francisco  Austin
0 2011-10-01      63.4           62.7    72.2
1 2011-10-02      58.0           59.9    67.7
2 2011-10-03      53.3           59.1    69.4
3 2011-10-04      55.7           58.8    68.0
4 2011-10-05      64.2           58.7    72.4

melt処理


date      city  temperature
0 2011-10-01  New York         63.4
1 2011-10-02  New York         58.0
2 2011-10-03  New York         53.3
3 2011-10-04  New York         55.7
4 2011-10-05  New York         64.2

In [3]:
fig = px.line(
    melt_plot_df, x='date', y='temperature',
    color='city'
    )
fig.show()

Ploty Expressは高レベルのAPIのため、グラフの細かな設定ができないという欠点がある。<br>
graph_objectを使ってより精密なグラフを作成することができる。<br>

In [4]:
import plotly.graph_objects as go
fig = go.Figure()
for city in melt_plot_df['city'].unique():
    fig.add_trace(
        go.Scatter(
            x=melt_plot_df[melt_plot_df['city'] == city]['date'],
            y=melt_plot_df[melt_plot_df['city']==city]['temperature'],
            name=city
            )
        )

fig.update_layout(
    xaxis=dict(title='date'),
    yaxis=dict(title='Temperature[°F]')
    )

fig.show()

In [5]:
# 一気に作ってもOK
plot = []
for city in melt_plot_df['city'].unique():
        plot.append(go.Scatter(
            x=melt_plot_df[melt_plot_df['city'] == city]['date'],
            y=melt_plot_df[melt_plot_df['city']==city]['temperature'],
            name=city))

layout = go.Layout(
    title="City Temp.",
    width=900, height=500,
    font_size=15,
    hoverlabel_font_size=10,
    xaxis=dict(title="date", showline=True, linecolor="black", mirror=True),
    yaxis=dict(title="Temperature[°F]", showline=True, linecolor="black", mirror=True),
    plot_bgcolor="white",
    paper_bgcolor="white")

fig = go.Figure(data=plot, layout=layout)
fig.show()

In [6]:
from plotly.subplots import make_subplots
fig = make_subplots(
    rows=3, cols=1, # 行と列を設定
    subplot_titles=(melt_plot_df['city'].unique())  # タイトルは都市名を設定
    )

for i, city in enumerate(melt_plot_df['city'].unique()):
    fig.add_trace(
        go.Scatter(
            x=melt_plot_df[melt_plot_df['city'] == city]['date'],
            y=melt_plot_df[melt_plot_df['city']==city]['temperature'],
            name=city),
        row=i+1, col=1
        )

xdict, ydict = {}, {}
for key in [1, 2, 3]:
    xdict[f'xaxis{key}'] = dict(title='date')
    ydict[f'yaxis{key}'] = dict(title='temperature[F]')

fig.update_layout(
    width=900, height=800,
    showlegend=False,
    **xdict,
    **ydict
    )
# xaxis = dict{title=''}, xaxis2 = dict{title=''}...のようにする
fig.show()

# 散布図
2つの数値を座標として捉えたときのデータの偏りを調べる方法。1つの系列が自国の場合はX軸を時刻に割り当てる場合が多い。3つめの数値があるときは点の代償などで大小を表現することができる。ただし、見る人が対象となるラベルを見つけなければならないため、折れ線グラフや時系列ヒートマップのように時間的な数値の増減を表現するのは苦手。あくまで、「どこに偏りがあるか？」を見るのに使う。<br>
データはボストンの住宅価格データセットを用いた。
- CRIM： 町別の「犯罪率」
- ZN： 25,000平方フィートを超える区画に分類される住宅地の割合＝「広い家の割合」
- INDUS： 町別の「非小売業の割合」
- CHAS： チャールズ川のダミー変数（区画が川に接している場合は1、そうでない場合は0）＝「川の隣か」
- NOX： 「NOx濃度（0.1ppm単位）」＝一酸化窒素濃度（parts per 10 million単位）。この項目を目的変数とする場合もある
- RM： 1戸当たりの「平均部屋数」
- AGE： 1940年より前に建てられた持ち家の割合＝「古い家の割合」
- DIS： 5つあるボストン雇用センターまでの加重距離＝「主要施設への距離」
- RAD： 「主要高速道路へのアクセス性」の指数
- TAX： 10,000ドル当たりの「固定資産税率」
- PTRATIO： 町別の「生徒と先生の比率」
- B： 「1000(Bk - 0.63)」の二乗値。Bk＝「町ごとの黒人の割合」を指す
- LSTAT： 「低所得者人口の割合」
- MEDV：「住宅価格」（1000ドル単位）の中央値。通常はこの数値が目的変数として使われる

カラーマップ：https://plotly.com/python/builtin-colorscales/

In [7]:
scatter_df = pd.read_csv('data/scatter.csv')
display(scatter_df.head())

# plolty.expressを使った方法
fig = px.scatter(
    data_frame=scatter_df, x='rm', y='lstat',
    color='medv',  # 'medv'の値によって色味を変える
    size='medv'   # 'medv'の値によってサイズを変える
    )

fig.update_layout(
    width=800, height=600,
    title='Boston house price [medv]',
    font=dict(size=18)
    )

fig.show()

crim    zn  indus  chas    nox     rm   age     dis  rad  tax  ptratio  \
0  0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900    1  296     15.3   
1  0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671    2  242     17.8   
2  0.02729   0.0   7.07     0  0.469  7.185  61.1  4.9671    2  242     17.8   
3  0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622    3  222     18.7   
4  0.06905   0.0   2.18     0  0.458  7.147  54.2  6.0622    3  222     18.7   

        b  lstat  medv  
0  396.90   4.98  24.0  
1  396.90   9.14  21.6  
2  392.83   4.03  34.7  
3  394.63   2.94  33.4  
4  396.90   5.33  36.2

In [8]:
# graph.objectを使った方法
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=scatter_df["rm"], y=scatter_df["lstat"],
        mode='markers',
        marker=dict(size=scatter_df["medv"]/3,  # 所得が大きいほどmarkerが大きくなる
        color=scatter_df["medv"],  # 所得が大きいほど色が濃くなる
        colorscale='reds',
        showscale=True) # scaleを表示
        )
    )

fig.update_layout(
    width=800, height=600,
    title='Boston house price [medv]',
    xaxis=dict(title='average number of rooms per dweling [rm]'),
    yaxis=dict(title='lower status of the population [lstat]'),
    font=dict(size=18)
    )

fig.show()

In [9]:
scatter = go.Scatter(
    x=scatter_df["rm"],
    y=scatter_df["lstat"],
    mode="markers",
    marker=dict(
        size=scatter_df["medv"]/3,
        color=scatter_df['medv'],
        colorscale="reds",
        showscale=True)
    )

layout = go.Layout(
    width=700,
    height=500,
    title='Boston house price [medv]',
    xaxis=dict(title='average number of rooms per dweling [rm]'),
    yaxis=dict(title='lower status of the population [lstat]'),
    font=dict(size=18))

fig = go.Figure(data=scatter, layout=layout)
fig.show()

# ヒートマップ
数値2つを座標として、3つ目の数値をその座標の色を決定するために使うことで、全体の数値のバラつきや、高い・低い値の集中しているエリアを知ることができる。数値の代わりに時刻にすることもできなくはないが、あまりそういうグラフは見たことがない。<br>
データはhttps://github.com/mwaskom/seaborn-data/blob/master/flights.csv からのもので、各年の各月における飛行機の乗客数

In [10]:
heatmap_df = pd.read_csv('data/heatmap.csv')
heatmap_df.head()

year     month  passengers
0  1949   January         112
1  1949  February         118
2  1949     March         132
3  1949     April         129
4  1949       May         121

In [11]:
year = heatmap_df['year'].unique()
month = heatmap_df['month'].unique()
passengers = heatmap_df['passengers'].to_numpy().reshape(month.size, year.size).T

In [12]:
# plotly.expressを使った方法
fig = px.imshow(
    passengers, x=year, y=month,
    text_auto=True,
    aspect='auto'
)
fig.update_layout(width=800, height=800)
fig.show()

In [13]:
# graph.objectを使った方法(annotationがなぜかできない)
fig = go.Figure()
fig.add_trace(go.Heatmap(
    x=year, y=month[::-1], z=passengers, 
    text=passengers,
    textfont=dict(size=18)
))
fig.update_layout(
    width=800, height=800,
    xaxis=dict(title='year'),
    yaxis=dict(title='month')
)
fig.update_xaxes(tickvals=list(year))
fig.show()

In [14]:
# figure_factoryを使った方法
import plotly.figure_factory as ff

fig = ff.create_annotated_heatmap(
    x=year.tolist(), y=month.tolist(),
    z=passengers,
    annotation_text=passengers
)
fig.update_layout(
    width=800, height=800,
    xaxis=dict(title='year'),
    yaxis=dict(title='month')
)
fig.update_xaxes(tickvals=list(year))

fig.show()

# 積み重ね棒グラフ/集合棒グラフ
2つのラベルと1つの数値があったときに、これらの数値の大小を比較する方法。2つ以上のラベルをうまく表現できる数少ない方法だと思うが、データ数（≒2つのラベルの組み合わせ数）が50を超えたぐらいから図が煩雑になって読み取りが難しくなってしまう。<br>
データはhttps://www.enecho.meti.go.jp/about/whitepaper/2014html/2-1-1.html からのもので、日本の一次エネルギー国内供給の推移である。

In [15]:
stacked_bar_df = pd.read_csv('data/stacked_bar_chart.csv')
stacked_bar_df.head()

年度    石油    石炭  天然ガス   原子力    水力  新エネルギー・地熱等
0  1965  3.56  1.87  0.08  0.00  0.75        0.11
1  1966  4.13  1.92  0.09  0.01  0.77        0.11
2  1967  5.11  2.29  0.09  0.01  0.67        0.11
3  1968  5.95  2.42  0.10  0.01  0.72        0.12
4  1969  7.19  2.59  0.12  0.01  0.73        0.13

In [16]:
# plotly.expressを利用

stacked_bar_px_df = stacked_bar_df.melt(
    id_vars=['年度'],
    var_name='enegy_type',
    value_name='supply'
    )

display(stacked_bar_px_df.head())

fig = px.bar(stacked_bar_px_df, x='年度', y='supply', color='enegy_type')
fig.update_layout(
    width=1200, height=600,
    xaxis=dict(linecolor='black',
               mirror=True),
    yaxis=dict(title='国内供給量[10<sup>18</sup> J]',  # latexが書けないのでHTML形式で書く
               linecolor='black',
               gridcolor='gray',
               mirror=True),
    plot_bgcolor='white')

fig.show()

年度 enegy_type  supply
0  1965         石油    3.56
1  1966         石油    4.13
2  1967         石油    5.11
3  1968         石油    5.95
4  1969         石油    7.19

In [17]:
# graph.objectを利用①
fig = go.Figure()
for i in range(1, len(stacked_bar_df.columns)):
    fig.add_trace(go.Bar(name=stacked_bar_df.columns[i],
                         x=stacked_bar_df.iloc[:, 0],
                         y=stacked_bar_df.iloc[:, i]))

fig.update_layout(
    title='一次エネルギー国内供給の推移',
    xaxis=dict(title='年度'),
    yaxis=dict(title='国内供給量[10<sup>18</sup> J]'),
    barmode='stack',
    width=1200, height=600)

fig.show()

In [18]:
# graph.objectを利用②
data = [go.Bar(x=stacked_bar_df.iloc[:, 0],
               y=stacked_bar_df.iloc[:, i], name=stacked_bar_df.columns[i])
               for i in range(1, len(stacked_bar_df.columns))]

layout = go.Layout(
    title=dict(text='一次エネルギー国内供給の推移'),
    xaxis=dict(title='年度'),
    yaxis=dict(title=r"国内供給量 [10<sup>18</sup> J]"),
    barmode='stack',
    width=1200, height=600)

fig = go.Figure(data=data, layout=layout)
fig.show()

# 棒グラフ

データは東京の気温情報https://smart-hint.com/tokyo-temperature/ から

In [19]:
bar_df = pd.read_csv(
    'data/bar.csv', index_col=0, parse_dates=True,
    date_parser=lambda x: pd.to_datetime(x, format='%Y/%m/%d'))

bar_df.head()

平均気温  最高気温  最低気温  月
日付                             
2021-01-01   4.4  10.5  -1.3  1
2021-01-02   4.8  10.8   0.1  1
2021-01-03   3.7   8.4  -0.4  1
2021-01-04   5.8  11.4   1.3  1
2021-01-05   6.0  10.0   2.5  1

In [20]:
bar_df_px = bar_df.groupby("月").agg({"平均気温":["mean", "std"],
                                    "最高気温":["mean", "std"],
                                    "最低気温":["mean", "std"]}).reset_index()
bar_df_px = bar_df_px.melt(id_vars="月",
                           var_name=["temp_type", 'mean_or_std'],
                           value_name="temp")
bar_df_px

月 temp_type mean_or_std       temp
0    1      平均気温        mean   5.409677
1    2      平均気温        mean   8.450000
2    3      平均気温        mean  12.764516
3    4      平均気温        mean  15.106667
4    5      平均気温        mean  19.600000
..  ..       ...         ...        ...
67   8      最低気温         std   2.435618
68   9      最低気温         std   1.814577
69  10      最低気温         std   4.023135
70  11      最低気温         std   3.022386
71  12      最低気温         std   3.205811

[72 rows x 4 columns]

In [21]:
fig = px.bar(bar_df_px[bar_df_px["mean_or_std"]=="mean"], x='月', y='temp',
             error_y=bar_df_px[bar_df_px["mean_or_std"]=="std"].loc[:, "temp"],
             color='temp_type', barmode='group')

fig.update_layout(
    title='東京の気温(月別)',
    xaxis=dict(dtick=1)  # x軸を1月毎に表示に変更
    )

fig.show()

In [22]:
fig = go.Figure()
for i in bar_df.columns[:-1]:
    fig.add_trace(
        go.Bar(x=bar_df["月"].unique(),
               y=bar_df[i].resample("M").mean(),
               error_y=dict(type="data", array=bar_df[i].resample("M").std()),
               name=i))

fig.update_layout(
    title='東京の気温(月別)',
    xaxis=dict(dtick=1)  # x軸を1月毎に表示に変更
    )

# 円グラフ
円グラフは、円全体を100%として、その中に占める項目の構成比を扇形で表したグラフ。扇形の面積により構成比の大小がわかる。データは、時計の針の12時の位置から時計回りに、大きい順に並べ、「その他」はいくら大きくても、一番最後に表示する。あまり扇形が小さくなるとグラフが見にくくなるので、構成比が小さいものは、まとめて「その他」にしてしまった方がよい。<br>
データはhttps://gyokai-search.com/3-tsushin.html から

In [23]:
pie_df = pd.read_csv('data/pie_chart.csv', header=None)
pie_df.columns = ['会社', '売上']
pie_df.head()

会社      売上
0         NTT  121564
1  ソフトバンクグループ   62215
2        KDDI   54467
3      NTTドコモ   47138
4  フジ・メディア・HD    5250

In [24]:
fig = px.pie(pie_df, values='売上', names='会社')
fig.show()

In [25]:
fig = go.Figure()
fig.add_trace(
    go.Pie(
        labels=pie_df['会社'],
        values=pie_df['売上']
        )
    )
fig.show()

# 箱ヒゲ図
データの分散をあらわすための可視化。図中では線の両端が最小値・最大値。箱の左側が第1四分位点、赤と緑の間の線が中央値、右側が第3四分位点となる。これによってラベル毎に数値のばらつきがどの程度あるか？ということを概ね理解することができる。この箱の部分が狭いほどその範囲に数値が集中していることを意味し、箱が広いほど数値がばらついていると読み取ることができる。たまに平均値を算出して棒グラフで表現するグラフを見かけるが、それだと数値が一部に集中しているのか、それともばらけているのか、ということまで分からないため、データの性質を見るという目的なら箱ひげ図のほうが望ましい。<br>
データはhttps://www.geeksforgeeks.org/box-plot-visualization-with-pandas-and-seaborn/を使用

In [26]:
boxplot_df = pd.read_csv('data/box_plot.csv')
boxplot_df.head()

total_bill   tip     sex smoker  day    time  size
0       16.99  1.01  Female     No  Sun  Dinner     2
1       10.34  1.66    Male     No  Sun  Dinner     3
2       21.01  3.50    Male     No  Sun  Dinner     3
3       23.68  3.31    Male     No  Sun  Dinner     2
4       24.59  3.61  Female     No  Sun  Dinner     4

In [27]:
days_list = ['Thur', 'Fri', 'Sat', 'Sun']
boxplot_df['order'] = boxplot_df['day'].apply(lambda x: days_list.index(x))
boxplot_df = boxplot_df.sort_values('order')
boxplot_df.head()

total_bill   tip     sex smoker   day   time  size  order
121       13.42  1.68  Female     No  Thur  Lunch     2      0
133       12.26  2.00  Female     No  Thur  Lunch     2      0
132       11.17  1.50  Female     No  Thur  Lunch     2      0
131       20.27  2.83  Female     No  Thur  Lunch     2      0
130       19.08  1.50    Male     No  Thur  Lunch     2      0

In [28]:
fig = px.box(
    boxplot_df, x='day', y='total_bill', 
    category_orders={'day':['Thur', 'Fri', 'Sat', 'Sun']}
    )

fig.update_layout(width=900, height=600)
fig.show()

In [29]:
fig = px.box(
    boxplot_df, x='day', y='total_bill',
    color='smoker',
    facet_col='sex',
    category_orders={'day':['Thur', 'Fri', 'Sat', 'Sun']}
    )

fig.update_layout(width=1200, height=600)
fig.show()

In [30]:
# graph.layoutを利用
fig = go.Figure()

fig.add_trace(go.Box(x=boxplot_df['day'], y=boxplot_df['total_bill']))
fig.update_layout(
    width=900, height=600,
    xaxis=dict(title='day'),
    yaxis=dict(title='totall bill[$]'),
    font=dict(size=18)
    )
fig.show()


In [31]:
colors = ['red', 'blue']
from plotly.subplots import make_subplots
fig = make_subplots(rows=1, cols=2, subplot_titles=['Female', 'Male'])

for i, sex in enumerate(['Female', 'Male']):
    for smoker in ['No', 'Yes']:
        fig.add_trace(
            go.Box(
                x=boxplot_df[(boxplot_df['sex']==sex) & (boxplot_df['smoker']==smoker)]['day'],
                y=boxplot_df[(boxplot_df['sex']==sex) & (boxplot_df['smoker']==smoker)]['total_bill'],
                name=smoker
                ),
            row=1, col=i+1
            )
fig.update_layout(
    width=1200, height=600, boxmode='group',
    xaxis1=dict(title='day'),
    xaxis2=dict(title='day'),
    yaxis1=dict(title='totall bill[$]'),
    font=dict(size=18)
    )

fig.show()

# ヒストグラム
箱ひげ図と同じく、どのようにデータが分散しているかを表現する可視化手法。箱ひげ図では中央値や四分位点がどこにあるかを示すだけだったが、どのヒストグラムではどの数値帯にデータが何件（または全体データ数の何%）が出現したかを表現するため、データのばらつきが克明にわかる。基本的に1系列の数値データのみしか扱えないので複数のラベルについて調べたいという場合はラベル毎に別々にグラフを作成する必要があるが、数値データの性質を調べるためには強力な可視化手法。各数値帯を棒グラフ状に表す方法の他に折れ線グラフを使う方法、または累積度数分布として表現する方法などもある。
(ラベル, 数値)のようなデータ形式に対して、複数のラベルのヒストグラムを同じグラフに描画することもできるが、粒度の粗いデータだと線の重なりが起きたときなどに調整が必要なため、素直に1系列でグラフ化するのがお勧めである。
データはhttps://raw.githubusercontent.com/selva86/datasets/master/diamonds.csv

In [32]:
hist_df = pd.read_csv('data/histgram.csv')
hist_df.head()

carat      cut color clarity  depth  table  price     x     y     z
0   0.23    Ideal     E     SI2   61.5   55.0    326  3.95  3.98  2.43
1   0.21  Premium     E     SI1   59.8   61.0    326  3.89  3.84  2.31
2   0.23     Good     E     VS1   56.9   65.0    327  4.05  4.07  2.31
3   0.29  Premium     I     VS2   62.4   58.0    334  4.20  4.23  2.63
4   0.31     Good     J     SI2   63.3   58.0    335  4.34  4.35  2.75

In [33]:
# plotly.expressを利用 -> なぜかめちゃくちゃ重い
# px.histogram(
#     hist_df,
#     x='depth',
#     color='cut',
#     barmode='overlay',  # 透過して表示
#     marginal='box'  # 上に箱ひげ図を追加
#     )  

データの数が違うときは絶対値ベースではなく、密度ベースで議論することも大事なので密度表示を行う

In [34]:
# plotly.expressを利用（データの密度）
# px.histogram(
#     hist_df,
#     x='depth',
#     color='cut',
#     barmode='overlay',
#     histnorm='probability',  # データの密度ベースで表示
#     marginal='box'
#     )

In [35]:
# graph.objectを利用
fig = go.Figure()
for i, cut in enumerate(hist_df['cut'].unique()):
    fig.add_trace(
        go.Histogram(
            x=hist_df[hist_df['cut']==cut]['depth'],
            opacity=0.5,
            name=cut
            )
        )

fig.update_layout(
    barmode='overlay',
    xaxis=dict(title='depth'),
    yaxis=dict(title='count')
    )

fig.update_traces(
    xbins=dict(start=45, end=75, size=0.1)
    )
fig.show()

In [36]:
# カーネル密度推定を使ってフィッティング（処理は重い）
import plotly.figure_factory as ff
fig = ff.create_distplot([hist_df[hist_df['cut']==cut]['depth'] for cut in hist_df['cut'].unique()],
                         hist_df['cut'].unique(),
                         curve_type='normal',
                         bin_size=0.1)

fig.update_layout(barmode='overlay')
fig.show()

# 3次元　散布図
maplotlibやseabornでも可能だが、個人的にはインタラクティブに動かせるplotlyがおすすめ

In [37]:
scatter_3d_df = pd.read_csv('data/scatter.csv')
scatter_3d_df.head()

crim    zn  indus  chas    nox     rm   age     dis  rad  tax  ptratio  \
0  0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900    1  296     15.3   
1  0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671    2  242     17.8   
2  0.02729   0.0   7.07     0  0.469  7.185  61.1  4.9671    2  242     17.8   
3  0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622    3  222     18.7   
4  0.06905   0.0   2.18     0  0.458  7.147  54.2  6.0622    3  222     18.7   

        b  lstat  medv  
0  396.90   4.98  24.0  
1  396.90   9.14  21.6  
2  392.83   4.03  34.7  
3  394.63   2.94  33.4  
4  396.90   5.33  36.2

In [38]:
fig = px.scatter_3d(
    scatter_3d_df,
    x='rm', y='lstat', z='nox', 
    color='medv',
    size='medv'
    )
fig.update_layout(width=700, height=700)
fig.show()

In [39]:
fig = go.Figure()
fig.add_trace(
    go.Scatter3d(
        x=scatter_3d_df['rm'],
        y=scatter_3d_df['lstat'],
        z=scatter_3d_df['nox'],
        mode='markers',
        marker=dict(
            size=scatter_3d_df['medv']/5,
            opacity=0.8,  # 色を少し透明に
            color=scatter_3d_df['medv'],  # 所得が大きいほど色が濃くなる
            colorbar=dict(title='medv'),
            colorscale='Inferno'
            )
        )
    )

fig.update_layout(
    width=700, height=700,
    scene=dict(
        xaxis_title='rm',
        yaxis_title='lstat',
        zaxis_title='nox'
        ),
    font=dict(size=12)
    )

fig.show()

# 3次元　プロット

In [40]:
lines_3d_df = px.data.gapminder()
lines_3d_df.head()

country continent  year  lifeExp       pop   gdpPercap iso_alpha  \
0  Afghanistan      Asia  1952   28.801   8425333  779.445314       AFG   
1  Afghanistan      Asia  1957   30.332   9240934  820.853030       AFG   
2  Afghanistan      Asia  1962   31.997  10267083  853.100710       AFG   
3  Afghanistan      Asia  1967   34.020  11537966  836.197138       AFG   
4  Afghanistan      Asia  1972   36.088  13079460  739.981106       AFG   

   iso_num  
0        4  
1        4  
2        4  
3        4  
4        4

In [41]:
# データが多すぎるので大陸(+年代)で分ける
lines_3d_df = lines_3d_df.groupby(['continent', 'year']).mean().reset_index()
lines_3d_df

/var/folders/mw/h7f97pjd0b5ft_58lv82tdjc0000gn/T/ipykernel_75490/1603499360.py:2: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.



continent  year    lifeExp           pop     gdpPercap     iso_num
0     Africa  1952  39.135500  4.570010e+06   1252.572466  458.826923
1     Africa  1957  41.266346  5.093033e+06   1385.236062  458.826923
2     Africa  1962  43.319442  5.702247e+06   1598.078825  458.826923
3     Africa  1967  45.334538  6.447875e+06   2050.363801  458.826923
4     Africa  1972  47.450942  7.305376e+06   2339.615674  458.826923
5     Africa  1977  49.580423  8.328097e+06   2585.938508  458.826923
6     Africa  1982  51.592865  9.602857e+06   2481.592960  458.826923
7     Africa  1987  53.344788  1.105450e+07   2282.668991  458.826923
8     Africa  1992  53.629577  1.267464e+07   2281.810333  458.826923
9     Africa  1997  53.598269  1.430448e+07   2378.759555  458.826923
10    Africa  2002  53.325231  1.603315e+07   2599.385159  458.826923
11    Africa  2007  54.806038  1.787576e+07   3089.032605  458.826923
12  Americas  1952  53.279840  1.380610e+07   4079.062552  393.720000
13  Americas  1957  55.960280  1.547816e+07   4616.043733  393.720000
14  Americas  1962  58.398760  1.733081e+07   4901.541870  393.720000
15  Americas  1967  60.410920  1.922986e+07   5668.253496  393.720000
16  Americas  1972  62.394920  2.117537e+07   6491.334139  393.720000
17  Americas  1977  64.391560  2.312271e+07   7352.007126  393.720000
18  Americas  1982  66.228840  2.521164e+07   7506.737088  393.720000
19  Americas  1987  68.090720  2.731016e+07   7793.400261  393.720000
20  Americas  1992  69.568360  2.957096e+07   8044.934406  393.720000
21  Americas  1997  71.150480  3.187602e+07   8889.300863  393.720000
22  Americas  2002  72.422040  3.399091e+07   9287.677107  393.720000
23  Americas  2007  73.608120  3.595485e+07  11003.031625  393.720000
24      Asia  1952  46.314394  4.228356e+07   5195.484004  404.666667
25      Asia  1957  49.318544  4.735699e+07   5787.732940  404.666667
26      Asia  1962  51.563223  5.140476e+07   5729.369625  404.666667
27      Asia  1967  54.663640  5.774736e+07   5971.173374  404.666667
28      Asia  1972  57.319269  6.518098e+07   8187.468699  404.666667
29      Asia  1977  59.610556  7.225799e+07   7791.314020  404.666667
30      Asia  1982  62.617939  7.909502e+07   7434.135157  404.666667
31      Asia  1987  64.851182  8.700669e+07   7608.226508  404.666667
32      Asia  1992  66.537212  9.494825e+07   8639.690248  404.666667
33      Asia  1997  68.020515  1.025238e+08   9834.093295  404.666667
34      Asia  2002  69.233879  1.091455e+08  10174.090397  404.666667
35      Asia  2007  70.728485  1.155138e+08  12473.026870  404.666667
36    Europe  1952  64.408500  1.393736e+07   5661.057435  427.633333
37    Europe  1957  66.703067  1.459635e+07   6963.012816  427.633333
38    Europe  1962  68.539233  1.534517e+07   8365.486814  427.633333
39    Europe  1967  69.737600  1.603930e+07  10143.823757  427.633333
40    Europe  1972  70.775033  1.668784e+07  12479.575246  427.633333
41    Europe  1977  71.937767  1.723882e+07  14283.979110  427.633333
42    Europe  1982  72.806400  1.770890e+07  15617.896551  427.633333
43    Europe  1987  73.642167  1.810314e+07  17214.310727  427.633333
44    Europe  1992  74.440100  1.860476e+07  17061.568084  427.633333
45    Europe  1997  75.505167  1.896480e+07  19076.781802  427.633333
46    Europe  2002  76.700600  1.927413e+07  21711.732422  427.633333
47    Europe  2007  77.648600  1.953662e+07  25054.481636  427.633333
48   Oceania  1952  69.255000  5.343003e+06  10298.085650  295.000000
49   Oceania  1957  70.295000  5.970988e+06  11598.522455  295.000000
50   Oceania  1962  71.085000  6.641759e+06  12696.452430  295.000000
51   Oceania  1967  71.310000  7.300207e+06  14495.021790  295.000000
52   Oceania  1972  71.910000  8.053050e+06  16417.333380  295.000000
53   Oceania  1977  72.855000  8.619500e+06  17283.957605  295.000000
54   Oceania  1982  74.290000  9.197425e+06  18554.709840  295.000000
55   Oceania  1987  75.320000  9.787208e+06  20448.040160  295.000000
56   Oceania 

In [42]:
fig = go.Figure()

for continent in lines_3d_df['continent'].unique():
    df_plot = lines_3d_df[lines_3d_df['continent']==continent]
    fig.add_trace(
        go.Scatter3d(
            x=df_plot['year'],
            y=df_plot['gdpPercap'],
            z=df_plot['lifeExp'],
            mode='lines',
            name=continent,
            line=dict(width=10)
        ) 
    )

fig.update_layout(
    width=700, height=700,
    scene=dict(
        xaxis_title='year',
        yaxis_title='gdpPercap',
        zaxis_title='lifeExp'
        ),
    font=dict(size=12)
    )

fig.show()

# Surface Plots

In [43]:
surface_df = pd.read_csv('data/surface.csv', index_col=0)
surface_df.head()

0         1          2          3          4          5         6  \
0  27.809850  49.61936  83.080670  116.66320  130.41400  150.72060  220.1871   
1  27.719660  48.55022  65.213740   95.27666  116.99640  133.90560  152.3412   
2  30.426700  33.47752  44.809530   62.47495   77.43523  104.21530  102.7393   
3  16.665490  30.10860  39.969520   44.12225   59.57512   77.56929  106.8925   
4   8.815617  18.35160   8.658275   27.58590   48.62691   60.18013   91.3286   

          7         8         9  ...        14        15        16         17  \
0  156.1536  148.6416  203.7845  ...  49.96142  21.89279  17.02552  11.743170   
1  151.9340  160.1139  179.5327  ...  33.08871  38.40972  44.24843  69.578600   
2  137.0004  186.0706  219.3173  ...  48.47132  74.71461  60.09090   7.073525   
3  166.5539  175.2381  185.2815  ...  60.55916  55.92124  15.17284   8.248324   
4  145.7109  116.0653  106.2662  ...  47.42691  69.20731  44.95468  29.171970   

          18         19         20         21         22         23  
0  14.752260  13.667100   5.677561   3.312340   1.156517  -0.147662  
1   4.019351   3.050024   3.039719   2.996142   2.967954   1.999594  
2   6.089851   6.537450   6.666096   7.306965   5.736840   3.625628  
3  36.680870  61.934130  20.268670  68.588190  46.498120   0.236010  
4  17.916740  16.255150  14.655590  17.260480  31.222450  46.717040  

[5 rows x 24 columns]

In [44]:
fig = go.Figure()
fig.add_trace(
    go.Surface(
        z=surface_df.values,
        contours_z=dict(
            show=True,  # z次元に関する輪郭線を描画するか否か
            usecolormap=True,  # 輪郭線をcolorscaleを用いるかどうか
            highlightcolor='limegreen',  # 輪郭線の色
            project_z=True)  # z軸に対して投影するかどうか
        )
    )

fig.update_layout(
    title='Bruno山の標高',
    scene_camera_eye=dict(
        x=1.87,
        y=0.88,
        z=-0.5)
    )
fig.show()

# コーンプロット

In [45]:
cone_df = pd.read_csv('data/cone_plot.csv', index_col=0)
cone_df.head()

x         y          z         u         v         w
0 -7.139517 -8.664006 -14.882418  0.636596 -0.324044 -0.250674
1 -5.244624 -6.927187 -14.352216  0.636745 -0.192036 -0.018775
2 -6.843954 -7.609499 -14.326971  0.691551 -0.265829 -0.211761
3 -4.897059 -7.083337 -11.078107  0.671394 -0.289265  0.099909
4 -3.030331 -6.394363 -10.957766  0.689872 -0.170497  0.155504

In [46]:
fig = go.Figure()
fig.add_trace(
    go.Cone(
        x=cone_df['x'], y=cone_df['y'], z=cone_df['z'],  # 3次元座標
        u=cone_df['u'], v=cone_df['v'], w=cone_df['w'],  # ベクトル場の座標
        colorscale='Greens',
        sizemode='absolute',
        sizeref=50
        )
    )